api.openweathermap.org/data/2.5/forecast/daily?lat={lat}&lon={lon}&cnt={cnt}&appid={API key}

By geographic coordinates
You can seach 16 day weather forecast with daily average parameters by geographic coordinats. All weather data can be obtained in JSON and XML formats.

In [1]:
import datetime
import sqlalchemy as sqla
from sqlalchemy import create_engine
import traceback
import glob
import os
import requests
import time
import json

In [2]:
# secrets.py file where i store sensitive info
import my_secrets

In [3]:
# mysql driver
import pymysql

In [4]:
# initialise environment variables
WEATHERKEY = os.environ.get("WEATHERKEY")
DB_USER = os.environ.get("DB_USER")
DB_PASS = os.environ.get("DB_PASS")
DB_URL = os.environ.get("DB_URL")

In [5]:
# variables to scrape forecast every half an hour
forecast_max = 16
forecast_count = forecast_max

In [6]:
# create connection to database using environment variables
# initialise as global variable so all functions can use it
print(DB_USER, DB_PASS, DB_URL)
engine = create_engine("mysql+pymysql://{0}:{1}@{2}".format(my_secrets.DB_USER, my_secrets.DB_PASS, my_secrets.DB_URI), echo=True)
connection = engine.connect()
print(os.path)
print(os.path.abspath(os.getcwd()))

None None None
2021-03-23 11:09:52,159 INFO sqlalchemy.engine.base.Engine SHOW VARIABLES LIKE 'sql_mode'
2021-03-23 11:09:52,160 INFO sqlalchemy.engine.base.Engine {}
2021-03-23 11:09:52,274 INFO sqlalchemy.engine.base.Engine SHOW VARIABLES LIKE 'lower_case_table_names'
2021-03-23 11:09:52,274 INFO sqlalchemy.engine.base.Engine {}
2021-03-23 11:09:52,500 INFO sqlalchemy.engine.base.Engine SELECT DATABASE()
2021-03-23 11:09:52,501 INFO sqlalchemy.engine.base.Engine {}
2021-03-23 11:09:52,721 INFO sqlalchemy.engine.base.Engine show collation where `Charset` = 'utf8mb4' and `Collation` = 'utf8mb4_bin'
2021-03-23 11:09:52,722 INFO sqlalchemy.engine.base.Engine {}
2021-03-23 11:09:52,840 INFO sqlalchemy.engine.base.Engine SELECT CAST('test plain returns' AS CHAR(60)) AS anon_1
2021-03-23 11:09:52,842 INFO sqlalchemy.engine.base.Engine {}
2021-03-23 11:09:52,957 INFO sqlalchemy.engine.base.Engine SELECT CAST('test unicode returns' AS CHAR(60)) AS anon_1
2021-03-23 11:09:52,959 INFO sqlalchem

In [7]:
print(os.path)
print(os.path.abspath(os.getcwd()))
print(my_secrets.DB_USER)
print(my_secrets.DB_PASS)
print(my_secrets.DB_URI)

<module 'ntpath' from 'C:\\Users\\tomcl\\anaconda3\\lib\\ntpath.py'>
C:\Users\tomcl\OneDrive\Documents\College\HDipComputerScience\SemesterTwo2021\SoftwareEngineering\MyWork\GroupProject\dublin_bikes
tom
comp30830_Tom
dublinbikes.coxfpldporqi.us-east-1.rds.amazonaws.com


In [8]:
# 16 day weather forcast table 
sql_create_table_weather_current = """
CREATE TABLE IF NOT EXISTS `dublin_bikes`.`weather_16DayFcast` (
time_queried DATETIME,
last_update DATETIME,
temp_day FLOAT,
temp_night FLOAT,
temp_eve FLOAT,
temp_morn FLOAT,
feels_like_day FLOAT,
feels_like_night FLOAT,
feels_like_eve FLOAT,
feels_like_morn FLOAT,
pressure FLOAT,
humidity FLOAT,
weather_main VARCHAR(256),
weather_description VARCHAR(256),
speed FLOAT,
deg FLOAT,
clouds FLOAT,
pop FLOAT
)
"""


In [9]:
# try to create both tables
def create_table():
    """
    Function to create 16 day table
    Only needs to be run once
    """
    try:
        res = engine.execute("DROP TABLE IF EXISTS `dublin_bikes`.`weather_16DayFcast`")
        res = engine.execute(sql_create_table_weather_current)
        print(res.fetchall())
    except Exception as e:
        print(e)



In [10]:
def get_data(data):
    """
    this function takes in the data and station number as input and returns a tuple with that data
    """
    now = datetime.datetime.utcnow()
    
    return (now, datetime.datetime.fromtimestamp(data.get("dt")), data.get("temp").get("day"), data.get("temp").get("night"),\
            data.get("temp").get("eve"), data.get("temp").get("morn"),data.get("feels_like").get("day"), data.get("feels_like").get("night"),\
            data.get("feels_like").get("eve"), data.get("feels_like").get("morn"), data.get("pressure"), data.get("humidity"),\
            data.get("weather")[0].get("main"), data.get("weather")[0].get("description"),\
            data.get("speed"), data.get("deg"), data.get("clouds"), data.get("pop"))


In [12]:
'''CHANGE 1 FROM MY SECRETS'''

def SixteenDay():
    """
    Gets 16 day weather forecast and imports into the data to database
    """
    print(my_secrets.WAPIKEY)
    r = requests.get(f"https://api.openweathermap.org/data/2.5/forecast/daily?lat=53.344004&lon=-6.26812&cnt=16&appid={my_secrets.WAPIKEY}")
    data = json.loads(r.text)
    days = data.get("list")
    print(data)
                     
    for day in days:
        vals = get_data(day) # get data function returns tuple of values
        print(vals)
        engine.execute("INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)", vals)
    return

In [ ]:
def main():
    global forecast_count
    # run create tables once
    create_table()
    #print(os.path)
    while True:
        try:
            SixteenDay()
            # forecast_count += 1
            time.sleep(60 * 60 * 24)
        except:
            print(traceback.format_exc())
            print("Error found an error when querying")
            time.sleep(60 * 60 * 24)
            # if engine is None:
            # pass

if __name__ == "__main__":
    main()

2021-03-23 11:09:54,079 INFO sqlalchemy.engine.base.Engine DROP TABLE IF EXISTS `dublin_bikes`.`weather_16DayFcast`
2021-03-23 11:09:54,081 INFO sqlalchemy.engine.base.Engine {}
2021-03-23 11:09:54,201 INFO sqlalchemy.engine.base.Engine COMMIT
2021-03-23 11:09:54,424 INFO sqlalchemy.engine.base.Engine 
CREATE TABLE IF NOT EXISTS `dublin_bikes`.`weather_16DayFcast` (
time_queried DATETIME,
last_update DATETIME,
temp_day FLOAT,
temp_night FLOAT,
temp_eve FLOAT,
temp_morn FLOAT,
feels_like_day FLOAT,
feels_like_night FLOAT,
feels_like_eve FLOAT,
feels_like_morn FLOAT,
pressure FLOAT,
humidity FLOAT,
weather_main VARCHAR(256),
weather_description VARCHAR(256),
speed FLOAT,
deg FLOAT,
clouds FLOAT,
pop FLOAT
)

2021-03-23 11:09:54,425 INFO sqlalchemy.engine.base.Engine {}
2021-03-23 11:09:54,698 INFO sqlalchemy.engine.base.Engine COMMIT
This result object does not return rows. It has been closed automatically.
768c306b20894c7bc8def5ebacb4e3c2
{'city': {'id': 2964574, 'name': 'Dublin', 'coor

2021-03-23 11:09:55,134 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 23, 11, 9, 55, 132422), datetime.datetime(2021, 3, 23, 12, 0), 283.31, 278.4, 283.72, 278.78, 277.23, 275.06, 277.96, 275, 1017, 67, 'Rain', 'light rain', 6.88, 210, 86, 0.98)
2021-03-23 11:09:55,278 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 23, 11, 9, 55, 517239), datetime.datetime(2021, 3, 24, 12, 0), 283.49, 279.12, 282.3, 278.28, 277.47, 274.93, 277.81, 273.55, 1017, 56, 'Rain', 'light rain', 6.19, 244, 42, 0.67)
2021-03-23 11:09:55,517 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-23 11:09:55,518 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 23, 11, 9, 55, 517239), datetime.datetime(2021, 3, 24, 12, 0), 283.49, 279.12, 282.3, 278.28, 277.47, 274.93, 277.81, 273.55, 1017, 56, 'Rain', 'light rain', 6.19, 244, 42, 0.67)
2021-03-23 11:09:55,648 INFO 

2021-03-23 11:09:59,957 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 23, 11, 9, 59, 956222), datetime.datetime(2021, 4, 4, 13, 0), 279.02, 279.58, 279.61, 278.4, 272.13, 274.26, 273.82, 274.6, 1024, 85, 'Rain', 'light rain', 7.84, 79, 97, 0.48)
2021-03-23 11:10:00,070 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 23, 11, 10, 0, 300449), datetime.datetime(2021, 4, 5, 13, 0), 283.07, 279.29, 281.15, 274.72, 278.79, 275.78, 277.12, 271.08, 1017, 55, 'Rain', 'light rain', 3.56, 307, 16, 0.45)
2021-03-23 11:10:00,300 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-23 11:10:00,301 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 23, 11, 10, 0, 300449), datetime.datetime(2021, 4, 5, 13, 0), 283.07, 279.29, 281.15, 274.72, 278.79, 275.78, 277.12, 271.08, 1017, 55, 'Rain', 'light rain', 3.56, 307, 16, 0.45)
2021-03-23 11:10:00,436 INFO 

2021-03-23 11:11:01,732 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 23, 11, 11, 1, 732703), datetime.datetime(2021, 3, 23, 12, 0), 283.31, 278.4, 283.72, 278.78, 277.23, 275.06, 277.96, 275, 1017, 67, 'Rain', 'light rain', 6.88, 210, 86, 0.98)
2021-03-23 11:11:01,844 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 23, 11, 11, 2, 69859), datetime.datetime(2021, 3, 24, 12, 0), 283.49, 279.12, 282.3, 278.28, 277.47, 274.93, 277.81, 273.55, 1017, 56, 'Rain', 'light rain', 6.19, 244, 42, 0.67)
2021-03-23 11:11:02,069 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-23 11:11:02,070 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 23, 11, 11, 2, 69859), datetime.datetime(2021, 3, 24, 12, 0), 283.49, 279.12, 282.3, 278.28, 277.47, 274.93, 277.81, 273.55, 1017, 56, 'Rain', 'light rain', 6.19, 244, 42, 0.67)
2021-03-23 11:11:02,183 INFO sq

2021-03-23 11:11:06,115 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 23, 11, 11, 6, 114415), datetime.datetime(2021, 4, 4, 13, 0), 279.02, 279.58, 279.61, 278.4, 272.13, 274.26, 273.82, 274.6, 1024, 85, 'Rain', 'light rain', 7.84, 79, 97, 0.48)
2021-03-23 11:11:06,225 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 23, 11, 11, 6, 466398), datetime.datetime(2021, 4, 5, 13, 0), 283.07, 279.29, 281.15, 274.72, 278.79, 275.78, 277.12, 271.08, 1017, 55, 'Rain', 'light rain', 3.56, 307, 16, 0.45)
2021-03-23 11:11:06,466 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-23 11:11:06,467 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 23, 11, 11, 6, 466398), datetime.datetime(2021, 4, 5, 13, 0), 283.07, 279.29, 281.15, 274.72, 278.79, 275.78, 277.12, 271.08, 1017, 55, 'Rain', 'light rain', 3.56, 307, 16, 0.45)
2021-03-23 11:11:06,609 INFO 

...

2021-03-24 06:14:25,157 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 14, 25, 149320), datetime.datetime(2021, 4, 5, 13, 0), 280.04, 278.82, 278.87, 277.86, 274.7, 270.5, 271.13, 273.57, 1020, 69, 'Rain', 'light rain', 5.14, 22, 100, 0.77)
2021-03-24 06:14:25,375 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 24, 6, 14, 25, 581316), datetime.datetime(2021, 4, 6, 13, 0), 278.68, 276.92, 278.14, 276.63, 270.66, 270.3, 270.97, 269.08, 1024, 63, 'Snow', 'light snow', 8.43, 42, 99, 0.37)
2021-03-24 06:14:25,581 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-24 06:14:25,589 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 14, 25, 581316), datetime.datetime(2021, 4, 6, 13, 0), 278.68, 276.92, 278.14, 276.63, 270.66, 270.3, 270.97, 269.08, 1024, 63, 'Snow', 'light snow', 8.43, 42, 99, 0.37)
2021-03-24 06:14:25,686 INFO sql

2021-03-24 06:15:26,946 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 15, 26, 935187), datetime.datetime(2021, 3, 24, 12, 0), 284.16, 279.06, 281.84, 279.07, 278.29, 275, 276.27, 274.25, 1016, 58, 'Rain', 'light rain', 6.25, 228, 41, 0.61)
2021-03-24 06:15:27,035 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 24, 6, 15, 27, 326234), datetime.datetime(2021, 3, 25, 12, 0), 285.06, 281.81, 283.41, 279.43, 279.1, 275.12, 277.48, 275.43, 1011, 69, 'Rain', 'light rain', 7.32, 212, 95, 0.67)
2021-03-24 06:15:27,326 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-24 06:15:27,326 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 15, 27, 326234), datetime.datetime(2021, 3, 25, 12, 0), 285.06, 281.81, 283.41, 279.43, 279.1, 275.12, 277.48, 275.43, 1011, 69, 'Rain', 'light rain', 7.32, 212, 95, 0.67)
2021-03-24 06:15:27,426 INFO

2021-03-24 06:15:32,041 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 15, 32, 36112), datetime.datetime(2021, 4, 5, 13, 0), 280.04, 278.82, 278.87, 277.86, 274.7, 270.5, 271.13, 273.57, 1020, 69, 'Rain', 'light rain', 5.14, 22, 100, 0.77)
2021-03-24 06:15:32,132 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 24, 6, 15, 32, 332000), datetime.datetime(2021, 4, 6, 13, 0), 278.68, 276.92, 278.14, 276.63, 270.66, 270.3, 270.97, 269.08, 1024, 63, 'Snow', 'light snow', 8.43, 42, 99, 0.37)
2021-03-24 06:15:32,332 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-24 06:15:32,336 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 15, 32, 332000), datetime.datetime(2021, 4, 6, 13, 0), 278.68, 276.92, 278.14, 276.63, 270.66, 270.3, 270.97, 269.08, 1024, 63, 'Snow', 'light snow', 8.43, 42, 99, 0.37)
2021-03-24 06:15:32,436 INFO sqla

2021-03-24 06:16:33,435 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 16, 33, 435311), datetime.datetime(2021, 3, 24, 12, 0), 284.16, 279.06, 281.84, 279.07, 278.29, 275, 276.27, 274.25, 1016, 58, 'Rain', 'light rain', 6.25, 228, 41, 0.61)
2021-03-24 06:16:33,537 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 24, 6, 16, 33, 745282), datetime.datetime(2021, 3, 25, 12, 0), 285.06, 281.81, 283.41, 279.43, 279.1, 275.12, 277.48, 275.43, 1011, 69, 'Rain', 'light rain', 7.32, 212, 95, 0.67)
2021-03-24 06:16:33,745 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-24 06:16:33,745 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 16, 33, 745282), datetime.datetime(2021, 3, 25, 12, 0), 285.06, 281.81, 283.41, 279.43, 279.1, 275.12, 277.48, 275.43, 1011, 69, 'Rain', 'light rain', 7.32, 212, 95, 0.67)
2021-03-24 06:16:33,845 INFO

2021-03-24 06:16:37,791 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 16, 37, 791311), datetime.datetime(2021, 4, 5, 13, 0), 280.04, 278.82, 278.87, 277.86, 274.7, 270.5, 271.13, 273.57, 1020, 69, 'Rain', 'light rain', 5.14, 22, 100, 0.77)
2021-03-24 06:16:37,887 INFO sqlalchemy.engine.base.Engine COMMIT
(datetime.datetime(2021, 3, 24, 6, 16, 38, 91275), datetime.datetime(2021, 4, 6, 13, 0), 278.68, 276.92, 278.14, 276.63, 270.66, 270.3, 270.97, 269.08, 1024, 63, 'Snow', 'light snow', 8.43, 42, 99, 0.37)
2021-03-24 06:16:38,091 INFO sqlalchemy.engine.base.Engine INSERT INTO `dublin_bikes`.`weather_16DayFcast` values(%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s,%s)
2021-03-24 06:16:38,091 INFO sqlalchemy.engine.base.Engine (datetime.datetime(2021, 3, 24, 6, 16, 38, 91275), datetime.datetime(2021, 4, 6, 13, 0), 278.68, 276.92, 278.14, 276.63, 270.66, 270.3, 270.97, 269.08, 1024, 63, 'Snow', 'light snow', 8.43, 42, 99, 0.37)
2021-03-24 06:16:38,185 INFO sqlal